In [6]:
import pandas as pd
import numpy as np
import os
import urllib.request
import subprocess
from tqdm import tqdm

In [15]:
# Define paths and URLs
PANEL_URL = 'http://ftp.1000genomes.ebi.ac.uk/vol1/ftp/release/20130502/integrated_call_samples_v3.20130502.ALL.panel'
DATA_DIR = '../data/1000g'
PANEL_PATH = f'{DATA_DIR}/integrated_call_samples.panel'
BASE_URL = 'http://ftp.1000genomes.ebi.ac.uk/vol1/ftp/release/20130502/'

In [5]:

# Create directory if not exists
os.makedirs(DATA_DIR, exist_ok=True)

# Download panel file if not exists
if not os.path.exists(PANEL_PATH):
    print(f"Downloading panel file from {PANEL_URL}")
    urllib.request.urlretrieve(PANEL_URL, PANEL_PATH)
    print("Download completed")
else:
    print("Panel file already exists")

# Read panel file
print("\nReading panel file...")
panel_data = pd.read_csv(PANEL_PATH, sep='\t')

# Define target populations (corresponding to HapMap3)
target_pops = ['ASW', 'CEU', 'CHB', 'JPT', 'LWK', 'MXL', 'TSI', 'YRI']

# 1. Display overall statistics
print("\n=== 1000 Genomes Phase 3 Overview ===")
print("\nSamples by super population:")
print(panel_data['super_pop'].value_counts())
print("\nSamples by population:")
print(panel_data['pop'].value_counts())

# 2. Analyze target populations
print("\n=== Target Populations Analysis ===")
pop_summary = []
for pop in target_pops:
    pop_data = panel_data[panel_data['pop'] == pop]
    summary = {
        'Population': pop,
        'Sample_Count': len(pop_data),
        'Super_Population': pop_data['super_pop'].iloc[0] if not pop_data.empty else 'Not Found',
        'Males': sum(pop_data['gender'] == 'male'),
        'Females': sum(pop_data['gender'] == 'female')
    }
    pop_summary.append(summary)
    
    print(f"\nPopulation: {pop}")
    print(f"Total samples: {summary['Sample_Count']}")
    print(f"Super population: {summary['Super_Population']}")
    print(f"Gender distribution: {summary['Males']} males, {summary['Females']} females")

# 3. Create summary DataFrame
summary_df = pd.DataFrame(pop_summary)
print("\n=== Summary Table ===")
print(summary_df)

# 4. Save files
# Save target sample IDs
target_samples = panel_data[panel_data['pop'].isin(target_pops)]
target_samples_path = f'{DATA_DIR}/target_samples.txt'
target_samples['sample'].to_csv(target_samples_path, index=False, header=False)
print(f"\nSaved {len(target_samples)} sample IDs to {target_samples_path}")

# Save population summary
summary_path = f'{DATA_DIR}/population_summary.csv'
summary_df.to_csv(summary_path, index=False)
print(f"Saved population summary to {summary_path}")

# 5. Print next steps
print("\n=== Next Steps ===")
print("1. Review the population summary above")
print("2. The target_samples.txt file can be used to filter VCF files")
print("3. Proceed with downloading VCF files for specific chromosomes")
print(f"Total samples to extract: {len(target_samples)}")

Panel file already exists

Reading panel file...

=== 1000 Genomes Phase 3 Overview ===

Samples by super population:
super_pop
AFR    661
EAS    504
EUR    503
SAS    489
AMR    347
Name: count, dtype: int64

Samples by population:
pop
GWD    113
YRI    108
IBS    107
TSI    107
CHS    105
JPT    104
PUR    104
GIH    103
CHB    103
STU    102
ITU    102
KHV     99
ESN     99
FIN     99
LWK     99
CEU     99
PJL     96
ACB     96
CLM     94
CDX     93
GBR     91
BEB     86
MSL     85
PEL     85
MXL     64
ASW     61
Name: count, dtype: int64

=== Target Populations Analysis ===

Population: ASW
Total samples: 61
Super population: AFR
Gender distribution: 26 males, 35 females

Population: CEU
Total samples: 99
Super population: EUR
Gender distribution: 49 males, 50 females

Population: CHB
Total samples: 103
Super population: EAS
Gender distribution: 46 males, 57 females

Population: JPT
Total samples: 104
Super population: EAS
Gender distribution: 56 males, 48 females

Population: LWK

In [16]:
def download_file(url, local_path, desc=None):
    """Download a file with progress bar"""
    if os.path.exists(local_path):
        print(f"File already exists: {local_path}")
        return
    
    print(f"Downloading: {url}")
    response = urllib.request.urlopen(url)
    total_size = int(response.headers.get('content-length', 0))
    
    with tqdm(total=total_size, unit='B', unit_scale=True, desc=desc) as pbar:
        urllib.request.urlretrieve(
            url, local_path,
            reporthook=lambda count, block_size, total_size: pbar.update(block_size)
        )

def download_chromosome(chrom):
    """Download VCF and index files for a specific chromosome"""
    # File naming pattern for Phase 3
    vcf_filename = f'ALL.chr{chrom}.phase3_shapeit2_mvncall_integrated_v5b.20130502.genotypes.vcf.gz'
    vcf_url = BASE_URL + vcf_filename
    vcf_path = os.path.join(DATA_DIR, vcf_filename)
    
    # Download VCF file
    download_file(vcf_url, vcf_path, f"Chromosome {chrom}")
    
    # Download index file
    download_file(vcf_url + '.tbi', vcf_path + '.tbi', f"Index chr{chrom}")
    
    return vcf_path

def filter_vcf(vcf_path, output_path, samples_file):
    """Filter VCF file to keep only target samples"""
    cmd = f'bcftools view -S {samples_file} -Oz -o {output_path} {vcf_path}'
    print(f"Filtering VCF file: {cmd}")
    subprocess.run(cmd, shell=True, check=True)
    
    # Index the filtered file
    cmd_index = f'bcftools index {output_path}'
    print("Creating index for filtered file")
    subprocess.run(cmd_index, shell=True, check=True)

# Let's start with chromosome 22 (smallest autosome)
if __name__ == "__main__":
    # Check if bcftools is installed
    try:
        subprocess.run(['bcftools', '--version'], capture_output=True)
        print("bcftools is installed")
    except FileNotFoundError:
        print("Error: bcftools is not installed. Please install it first.")
        print("You can install it using:")
        print("conda install -c bioconda bcftools")
        print("or")
        print("sudo apt-get install bcftools")
        exit(1)

    # Download chromosome 22
    chrom = 22
    vcf_path = download_chromosome(chrom)
    
    # Filter VCF for target samples
    samples_file = os.path.join(DATA_DIR, 'target_samples.txt')
    filtered_vcf = os.path.join(DATA_DIR, f'filtered.chr{chrom}.phase3.vcf.gz')
    
    filter_vcf(vcf_path, filtered_vcf, samples_file)
    
    print("\nProcess completed!")
    print(f"Filtered VCF file: {filtered_vcf}")

bcftools is installed
Downloading: http://ftp.1000genomes.ebi.ac.uk/vol1/ftp/release/20130502/ALL.chr22.phase3_shapeit2_mvncall_integrated_v5b.20130502.genotypes.vcf.gz


Chromosome 22: 206MB [02:12, 1.55MB/s]                                          


Downloading: http://ftp.1000genomes.ebi.ac.uk/vol1/ftp/release/20130502/ALL.chr22.phase3_shapeit2_mvncall_integrated_v5b.20130502.genotypes.vcf.gz.tbi


Index chr22: 49.2kB [00:00, 162kB/s]                                            


Filtering VCF file: bcftools view -S ../data/1000g/target_samples.txt -Oz -o ../data/1000g/filtered.chr22.phase3.vcf.gz ../data/1000g/ALL.chr22.phase3_shapeit2_mvncall_integrated_v5b.20130502.genotypes.vcf.gz
Creating index for filtered file

Process completed!
Filtered VCF file: ../data/1000g/filtered.chr22.phase3.vcf.gz


In [18]:
# check by small samples
# File paths
VCF_FILE = '../data/1000g/filtered.chr22.phase3.vcf.gz'
SAMPLES_FILE = '../data/1000g/target_samples.txt'

def verify_vcf():
    """Verify the filtered VCF file"""
    
    # 1. Check number of samples in filtered VCF
    cmd_samples = f"bcftools query -l {VCF_FILE}"
    result = subprocess.run(cmd_samples, shell=True, capture_output=True, text=True)
    samples = result.stdout.strip().split('\n')
    print(f"Number of samples in filtered VCF: {len(samples)}")
    
    # Compare with our target samples
    target_samples = pd.read_csv(SAMPLES_FILE, header=None)[0].tolist()
    print(f"Number of target samples: {len(target_samples)}")
    print(f"Samples match: {set(samples) == set(target_samples)}")
    
    # 2. Get basic stats about the VCF
    cmd_stats = f"bcftools stats {VCF_FILE} | grep '^SN'"
    result = subprocess.run(cmd_stats, shell=True, capture_output=True, text=True)
    print("\nVCF Statistics:")
    stats = result.stdout.strip().split('\n')
    for stat in stats:
        if 'number of records' in stat or 'number of SNPs' in stat:
            print(stat.split('\t')[2:][0])
    
    # 3. Check first few variants
    cmd_head = f"bcftools view {VCF_FILE} | head -n 20"
    result = subprocess.run(cmd_head, shell=True, capture_output=True, text=True)
    print("\nFirst few lines of VCF header:")
    header_lines = [line for line in result.stdout.split('\n') if line.startswith('#CHROM')]
    if header_lines:
        columns = header_lines[0].split('\t')
        print(f"Number of columns: {len(columns)}")
        print(f"Sample columns: {len(columns) - 9}")  # VCF has 9 fixed columns before samples

if __name__ == "__main__":
    print("Verifying filtered VCF file...")
    verify_vcf()

Verifying filtered VCF file...
Number of samples in filtered VCF: 745
Number of target samples: 745
Samples match: True

VCF Statistics:
number of records:
number of SNPs:

First few lines of VCF header:


SN	0	number of samples:	745\\
SN	0	number of records:	1103547\\
SN	0	number of no-ALTs:	0\\
SN	0	number of SNPs:	1060388\\
SN	0	number of MNPs:	0\\
SN	0	number of indels:	43230\\
SN	0	number of others:	801\\
SN	0	number of multiallelic sites:	6348\\
SN	0	number of multiallelic SNP sites:	4063

In [19]:
from concurrent.futures import ThreadPoolExecutor, as_completed
import time

# Constants
SAMPLES_FILE = os.path.join(DATA_DIR, 'target_samples.txt')

def download_file(url, local_path, desc=None):
    """Download a file with progress bar"""
    if os.path.exists(local_path):
        print(f"File already exists: {local_path}")
        return local_path
    
    try:
        response = urllib.request.urlopen(url)
        total_size = int(response.headers.get('content-length', 0))
        
        with tqdm(total=total_size, unit='B', unit_scale=True, desc=desc) as pbar:
            urllib.request.urlretrieve(
                url, local_path,
                reporthook=lambda count, block_size, total_size: pbar.update(block_size)
            )
        return local_path
    except Exception as e:
        print(f"Error downloading {url}: {e}")
        if os.path.exists(local_path):
            os.remove(local_path)
        return None

def process_chromosome(chrom):
    """Process a single chromosome: download and filter"""
    try:
        # File paths
        vcf_filename = f'ALL.chr{chrom}.phase3_shapeit2_mvncall_integrated_v5b.20130502.genotypes.vcf.gz'
        vcf_url = BASE_URL + vcf_filename
        vcf_path = os.path.join(DATA_DIR, vcf_filename)
        filtered_vcf = os.path.join(DATA_DIR, f'filtered.chr{chrom}.phase3.vcf.gz')
        
        # Skip if filtered file already exists
        if os.path.exists(filtered_vcf):
            print(f"Filtered file for chromosome {chrom} already exists")
            return chrom, True
        
        # Download VCF and index files
        print(f"Processing chromosome {chrom}")
        vcf_file = download_file(vcf_url, vcf_path, f"Chr{chrom} VCF")
        if vcf_file:
            index_file = download_file(vcf_url + '.tbi', vcf_path + '.tbi', f"Chr{chrom} Index")
            
            if index_file:
                # Filter VCF
                print(f"Filtering chromosome {chrom}")
                cmd = f'bcftools view -S {SAMPLES_FILE} -Oz -o {filtered_vcf} {vcf_path}'
                subprocess.run(cmd, shell=True, check=True)
                
                # Index filtered file
                cmd_index = f'bcftools index {filtered_vcf}'
                subprocess.run(cmd_index, shell=True, check=True)
                
                # Remove original VCF to save space
                os.remove(vcf_path)
                os.remove(vcf_path + '.tbi')
                
                return chrom, True
                
        return chrom, False
    except Exception as e:
        print(f"Error processing chromosome {chrom}: {e}")
        return chrom, False

def process_all_chromosomes():
    """Process all chromosomes in parallel"""
    # Create data directory if it doesn't exist
    os.makedirs(DATA_DIR, exist_ok=True)
    
    # Process chromosomes 1-22 in parallel
    chromosomes = range(1, 23)
    results = {}
    
    with ThreadPoolExecutor(max_workers=3) as executor:
        # Submit all chromosome processing tasks
        future_to_chrom = {executor.submit(process_chromosome, chrom): chrom 
                          for chrom in chromosomes}
        
        # Process results as they complete
        for future in as_completed(future_to_chrom):
            chrom, success = future.result()
            results[chrom] = success
    
    # Summary
    print("\nProcessing Summary:")
    successful = [chrom for chrom, success in results.items() if success]
    failed = [chrom for chrom, success in results.items() if not success]
    
    print(f"Successfully processed chromosomes: {successful}")
    if failed:
        print(f"Failed to process chromosomes: {failed}")
    
    # Verify all filtered files
    print("\nVerifying filtered files:")
    for chrom in chromosomes:
        filtered_vcf = os.path.join(DATA_DIR, f'filtered.chr{chrom}.phase3.vcf.gz')
        if os.path.exists(filtered_vcf):
            size = os.path.getsize(filtered_vcf) / (1024**3)  # Size in GB
            print(f"Chr{chrom}: {size:.2f} GB")

if __name__ == "__main__":
    start_time = time.time()
    
    print("Starting chromosome processing...")
    process_all_chromosomes()
    
    # Print total execution time
    duration = time.time() - start_time
    hours = int(duration // 3600)
    minutes = int((duration % 3600) // 60)
    seconds = int(duration % 60)
    print(f"\nTotal execution time: {hours}h {minutes}m {seconds}s")

Starting chromosome processing...
Processing chromosome 3
Processing chromosome 2
Processing chromosome 1


Chr3 VCF:   0%|                                     | 0.00/1.06G [00:00<?, ?B/s]
Chr1 VCF:   0%|                                     | 0.00/1.17G [00:00<?, ?B/s]

Chr3 VCF:   0%|                          | 8.19k/1.06G [00:00<6:44:08, 43.7kB/s]
Chr3 VCF:   0%|                           | 57.3k/1.06G [00:00<1:38:01, 180kB/s]

Chr2 VCF:   0%|                         | 8.19k/1.26G [00:00<18:04:54, 19.3kB/s]
Chr3 VCF:   0%|                              | 229k/1.06G [00:00<32:24, 544kB/s]

Chr2 VCF:   0%|                           | 57.3k/1.26G [00:00<2:59:39, 116kB/s]
Chr3 VCF:   0%|                             | 893k/1.06G [00:00<09:43, 1.81MB/s]

Chr2 VCF:   0%|                              | 229k/1.26G [00:00<49:57, 419kB/s]
Chr3 VCF:   0%|                            | 1.08M/1.06G [00:00<12:06, 1.46MB/s]

Chr2 VCF:   0%|                             | 827k/1.26G [00:00<15:07, 1.38MB/s]
Chr3 VCF:   0%|                            | 1.24M/1.06G [00:01<12:00, 1.47MB/s]
Chr1 VCF:   0%|        

Chr1 VCF:   2%|▍                           | 19.9M/1.17G [00:06<05:36, 3.40MB/s]

Chr3 VCF:   2%|▌                           | 20.6M/1.06G [00:06<07:51, 2.20MB/s]
Chr3 VCF:   2%|▌                           | 20.8M/1.06G [00:06<07:54, 2.19MB/s]

Chr2 VCF:   2%|▍                           | 20.5M/1.26G [00:06<06:38, 3.10MB/s]
Chr3 VCF:   2%|▌                           | 21.2M/1.06G [00:06<07:52, 2.20MB/s]

Chr2 VCF:   2%|▍                           | 21.0M/1.26G [00:06<05:49, 3.53MB/s]
Chr3 VCF:   2%|▌                           | 21.4M/1.06G [00:06<07:42, 2.24MB/s]
Chr1 VCF:   2%|▌                           | 21.4M/1.17G [00:06<05:35, 3.41MB/s]

Chr3 VCF:   2%|▌                           | 21.6M/1.06G [00:06<07:43, 2.24MB/s]
Chr1 VCF:   2%|▌                           | 21.7M/1.17G [00:06<05:31, 3.45MB/s]

Chr3 VCF:   2%|▌                           | 22.0M/1.06G [00:07<07:41, 2.25MB/s]
Chr1 VCF:   2%|▌                           | 22.1M/1.17G [00:07<05:50, 3.26MB/s]

Chr3 VCF:   2%|▌      

Chr3 VCF:   3%|▉                           | 33.7M/1.06G [00:11<06:52, 2.49MB/s]

Chr2 VCF:   3%|▊                           | 38.0M/1.26G [00:11<07:19, 2.77MB/s]
Chr1 VCF:   3%|▉                           | 37.9M/1.17G [00:12<06:29, 2.89MB/s]

Chr3 VCF:   3%|▉                           | 34.0M/1.06G [00:12<06:37, 2.58MB/s]
Chr1 VCF:   3%|▉                           | 38.2M/1.17G [00:12<06:33, 2.86MB/s]

Chr3 VCF:   3%|▉                           | 34.3M/1.06G [00:12<06:48, 2.51MB/s]
Chr1 VCF:   3%|▉                           | 38.6M/1.17G [00:12<06:02, 3.10MB/s]

Chr3 VCF:   3%|▉                           | 34.7M/1.06G [00:12<06:33, 2.61MB/s]
Chr1 VCF:   3%|▉                           | 39.0M/1.17G [00:12<05:35, 3.35MB/s]

Chr3 VCF:   3%|▉                           | 35.0M/1.06G [00:12<06:40, 2.56MB/s]
Chr1 VCF:   3%|▉                           | 39.4M/1.17G [00:12<06:01, 3.12MB/s]

Chr3 VCF:   3%|▉                           | 35.4M/1.06G [00:12<06:24, 2.66MB/s]

Chr2 VCF:   3%|▉     

Chr2 VCF:   4%|█▏                          | 52.7M/1.26G [00:17<08:48, 2.28MB/s]
Chr3 VCF:   5%|█▎                          | 50.5M/1.06G [00:17<07:42, 2.18MB/s]

Chr2 VCF:   4%|█▏                          | 52.9M/1.26G [00:17<08:58, 2.24MB/s]
Chr3 VCF:   5%|█▎                          | 50.7M/1.06G [00:17<08:04, 2.08MB/s]

Chr2 VCF:   4%|█▏                          | 53.2M/1.26G [00:17<09:24, 2.13MB/s]
Chr3 VCF:   5%|█▎                          | 51.0M/1.06G [00:17<08:02, 2.09MB/s]

Chr2 VCF:   4%|█▏                          | 53.5M/1.26G [00:17<08:41, 2.30MB/s]
Chr1 VCF:   5%|█▎                          | 52.8M/1.17G [00:17<08:05, 2.29MB/s]

Chr3 VCF:   5%|█▎                          | 51.2M/1.06G [00:18<08:43, 1.92MB/s]
Chr3 VCF:   5%|█▎                          | 51.4M/1.06G [00:18<08:45, 1.92MB/s]

Chr2 VCF:   4%|█▏                          | 54.0M/1.26G [00:18<09:18, 2.15MB/s]
Chr3 VCF:   5%|█▎                          | 51.6M/1.06G [00:18<08:47, 1.91MB/s]

Chr2 VCF:   4%|█▏     

...

Chr20 VCF:  94%|███████████████████████████▎ | 308M/327M [02:24<00:11, 1.63MB/s]
Chr20 VCF:  94%|███████████████████████████▎ | 308M/327M [02:24<00:11, 1.65MB/s]

Chr21 VCF:  87%|█████████████████████████▎   | 183M/210M [02:08<00:16, 1.68MB/s]
Chr20 VCF:  94%|███████████████████████████▎ | 308M/327M [02:24<00:10, 1.70MB/s]

Chr21 VCF:  87%|█████████████████████████▎   | 183M/210M [02:08<00:15, 1.70MB/s]
Chr20 VCF:  94%|███████████████████████████▎ | 309M/327M [02:24<00:11, 1.66MB/s]
Chr20 VCF:  94%|███████████████████████████▍ | 309M/327M [02:24<00:10, 1.69MB/s]

Chr21 VCF:  87%|█████████████████████████▎   | 183M/210M [02:09<00:15, 1.73MB/s]
Chr20 VCF:  94%|███████████████████████████▍ | 309M/327M [02:24<00:10, 1.73MB/s]

Chr21 VCF:  88%|█████████████████████████▍   | 184M/210M [02:09<00:15, 1.74MB/s]
Chr20 VCF:  95%|███████████████████████████▍ | 309M/327M [02:25<00:10, 1.71MB/s]

Chr21 VCF:  88%|█████████████████████████▍   | 184M/210M [02:09<00:14, 1.75MB/s]
Chr20 VCF:  95%|███████

Chr20 VCF:  99%|████████████████████████████▊| 325M/327M [02:30<00:00, 3.21MB/s]

Chr21 VCF:  95%|███████████████████████████▋ | 200M/210M [02:15<00:02, 4.35MB/s]
Chr20 VCF: 100%|████████████████████████████▊| 326M/327M [02:31<00:00, 3.46MB/s]

Chr21 VCF:  96%|███████████████████████████▋ | 201M/210M [02:15<00:01, 4.84MB/s]
Chr20 VCF: 100%|████████████████████████████▉| 326M/327M [02:31<00:00, 3.62MB/s]
Chr20 VCF: 100%|████████████████████████████▉| 326M/327M [02:31<00:00, 3.31MB/s]

Chr21 VCF:  96%|███████████████████████████▊ | 201M/210M [02:15<00:02, 3.93MB/s]
Chr20 VCF: 327MB [02:31, 2.16MB/s]                                              


Chr21 VCF:  96%|███████████████████████████▉ | 202M/210M [02:15<00:01, 5.04MB/s]

Chr21 VCF:  97%|████████████████████████████ | 203M/210M [02:15<00:01, 4.61MB/s]

Chr20 Index:   0%|                                  | 0.00/56.5k [00:00<?, ?B/s]

Chr20 Index:  15%|███▋                     | 8.19k/56.5k [00:00<00:01, 37.8kB/s]

Chr21 VCF:  97%|███

Filtering chromosome 20




Chr21 VCF:  98%|████████████████████████████▌| 206M/210M [02:16<00:00, 4.14MB/s]

Chr21 VCF:  99%|████████████████████████████▌| 207M/210M [02:16<00:00, 4.53MB/s]

Chr21 VCF:  99%|████████████████████████████▋| 207M/210M [02:16<00:00, 4.19MB/s]

Chr21 VCF:  99%|████████████████████████████▊| 208M/210M [02:17<00:00, 4.93MB/s]

Chr21 VCF:  99%|████████████████████████████▊| 209M/210M [02:17<00:00, 4.33MB/s]

Chr21 VCF: 210MB [02:17, 1.53MB/s]                                              
Chr21 Index: 49.2kB [00:00, 144kB/s]                                            


Filtering chromosome 21
Filtered file for chromosome 22 already exists

Processing Summary:
Successfully processed chromosomes: [3, 1, 2, 4, 6, 5, 9, 8, 7, 10, 12, 11, 14, 13, 15, 17, 16, 18, 19, 22, 21, 20]

Verifying filtered files:
Chr1: 0.44 GB
Chr2: 0.48 GB
Chr3: 0.40 GB
Chr4: 0.40 GB
Chr5: 0.36 GB
Chr6: 0.36 GB
Chr7: 0.33 GB
Chr8: 0.31 GB
Chr9: 0.24 GB
Chr10: 0.28 GB
Chr11: 0.28 GB
Chr12: 0.27 GB
Chr13: 0.20 GB
Chr14: 0.18 GB
Chr15: 0.17 GB
Chr16: 0.18 GB
Chr17: 0.16 GB
Chr18: 0.16 GB
Chr19: 0.13 GB
Chr20: 0.12 GB
Chr21: 0.08 GB
Chr22: 0.08 GB

Total execution time: 1h 8m 8s
